In [1]:
import os

while os.getcwd().split("/")[-1] != "alfa-hack-rag":
    os.chdir(os.path.abspath(os.path.join(os.getcwd(), "..")))

In [ ]:
import numpy as np
import pandas as pd
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from tqdm import tqdm

In [ ]:
df_websites = pd.read_csv("data/websites_updated.csv")
df_questions = pd.read_csv("data/questions_clean.csv")
df_sample = pd.read_csv("data/sample_submission.csv")

In [4]:
df_websites

web_id                                                url  kind  \
0          1                               https://alfabank.ru/  html   
1          2                        https://alfabank.ru/a-club/  html   
2          3               https://alfabank.ru/a-club/ultimate/  html   
3          4                 https://alfabank.ru/actions/rules/  html   
4          5                    https://alfabank.ru/alfafuture/  html   
...      ...                                                ...   ...   
1933    1934  https://alfabank.ru/help/t/retail/alfaforbusin...  html   
1934    1935  https://alfabank.ru/help/articles/investments/...  html   
1935    1936  https://alfabank.ru/make-money/investments/hel...  html   
1936    1937                https://alfabank.ru/everyday/smart/  html   
1937    1938           https://job.alfabank.ru/vacancies/moskva   NaN   

                                                  title  \
0     Альфа-Банк - кредитные и дебетовые карты, кред...   
1                         А-Клуб. Деньги имеют значение   
2                         А-Клуб. Деньги имеют значение   
3                                      Скидки по картам   
4     Альфа‑Будущее: Платформа для развития студенто...   
...                                                 ...   
1933  Как вернуть деньги покупателю и как рассчитыва...   
1934  Как вывести деньги с брокерского счёта — Альфа...   
1935      Пополнение и вывод средств — Альфа-Инвестиции   
1936                 Альфа-Смарт — подписка Альфа-Банка   
1937                                                NaN   

                                                   text  
0     Рассчитайте выгоду\nРасчёт калькулятора предва...  
1     Брокерские услуги\nОткрытие брокерского счёта ...  
2     Хотите получить больше информации?\nПозвоните ...  
3     Правила проведения Акции «Альфа Пятница. Бараб...  
4     Образование\nМагистратуры\nМагистратура ВШЭ\nМ...  
...                                                 ...  
1933  Возврат денег покупателю можно оформить через ...  
1934  Вывести деньги с брокерского счёта можно на ка...  
1935  Вывести деньги с брокерского счёта можно на сл...  
1936  Альфа-Смарт — семейная подписка, запущенная в ...  
1937                                                NaN  

[1938 rows x 5 columns]

In [5]:
def shorten(text, max_length=2048):
    return text[:max_length]  # Обрезка текста до максимальной длины

In [6]:
def embed_text(df, model_name, target_col, batch_size=32):
    model = SentenceTransformer(model_name)
    
    texts = df[target_col].fillna('').astype(str).apply(shorten).tolist()

    result = []
    for i in tqdm(range(0, len(texts), batch_size), desc="Encoding"):
        batch = texts[i:i+batch_size]
        emb = model.encode(batch, 
                          convert_to_numpy=True, 
                          normalize_embeddings=True)
        result.append(emb)
    
    result = np.vstack(result)
    
    # Создание новых колонок с эмбеддингами
    embedding_columns = [f'embedding_{i}' for i in range(result.shape[1])]
    df_with_embeddings = df.copy()
    df_with_embeddings[embedding_columns] = result
    
    return df_with_embeddings

In [7]:
sites = embed_text(df_websites, 'deepvk/USER2-small', 'text')
sites

Encoding: 100%|██████████| 61/61 [01:44<00:00,  1.71s/it]
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_with_embeddings[embedding_columns] = result
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_with_embeddings[embedding_columns] = result
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly f

web_id                                                url  kind  \
0          1                               https://alfabank.ru/  html   
1          2                        https://alfabank.ru/a-club/  html   
2          3               https://alfabank.ru/a-club/ultimate/  html   
3          4                 https://alfabank.ru/actions/rules/  html   
4          5                    https://alfabank.ru/alfafuture/  html   
...      ...                                                ...   ...   
1933    1934  https://alfabank.ru/help/t/retail/alfaforbusin...  html   
1934    1935  https://alfabank.ru/help/articles/investments/...  html   
1935    1936  https://alfabank.ru/make-money/investments/hel...  html   
1936    1937                https://alfabank.ru/everyday/smart/  html   
1937    1938           https://job.alfabank.ru/vacancies/moskva   NaN   

                                                  title  \
0     Альфа-Банк - кредитные и дебетовые карты, кред...   
1                         А-Клуб. Деньги имеют значение   
2                         А-Клуб. Деньги имеют значение   
3                                      Скидки по картам   
4     Альфа‑Будущее: Платформа для развития студенто...   
...                                                 ...   
1933  Как вернуть деньги покупателю и как рассчитыва...   
1934  Как вывести деньги с брокерского счёта — Альфа...   
1935      Пополнение и вывод средств — Альфа-Инвестиции   
1936                 Альфа-Смарт — подписка Альфа-Банка   
1937                                                NaN   

                                                   text  embedding_0  \
0     Рассчитайте выгоду\nРасчёт калькулятора предва...    -0.014753   
1     Брокерские услуги\nОткрытие брокерского счёта ...     0.001170   
2     Хотите получить больше информации?\nПозвоните ...    -0.051089   
3     Правила проведения Акции «Альфа Пятница. Бараб...    -0.023344   
4     Образование\nМагистратуры\nМагистратура ВШЭ\nМ...     0.068529   
...                                                 ...          ...   
1933  Возврат денег покупателю можно оформить через ...     0.000970   
1934  Вывести деньги с брокерского счёта можно на ка...     0.003429   
1935  Вывести деньги с брокерского счёта можно на сл...     0.016060   
1936  Альфа-Смарт — семейная подписка, запущенная в ...    -0.012279   
1937                                                NaN    -0.050933   

      embedding_1  embedding_2  embedding_3  embedding_4  ...  embedding_374  \
0        0.065041     0.084520     0.039943     0.072221  ...       0.006890   
1        0.133269     0.010313     0.001781     0.078007  ...       0.000192   
2        0.105189     0.016619    -0.019830     0.054395  ...      -0.013432   
3        0.077357    -0.022979    -0.037172    -0.019631  ...       0.018249   
4        0.067608     0.011570     0.046200     0.096194  ...      -0.000520   
...           ...          ...          ...          ...  ...            ...   
1933     0.057631     0.065661    -0.023415    -0.040953  ...      -0.004190   
1934     0.131681     0.037805    -0.060321     0.056517  ...       0.013054   
1935     0.116794     0.083178    -0.026272     0.060897  ...       0.000637   
1936     0.089811     0.051765    -0.015395    -0.002582  ...       0.005856   
1937     0.008528    -0.012867    -0.035781     0.029952  ...       0.002318   

      embedding_375  embedding_376  embedding_377  embedding_378  \
0          0.024198      -0.023604      -0.031784      -0.036770   
1         -0.002819      -0.034980      -0.008975       0.012451   
2          0.032335      -0.024349      -0.025228       0.000231   
3          0.006590      -0.019273       0.000508      -0.003307   
4          0.000474      -0.026957      -0.018580       0.000389   
...             ...            ...            ...            ...   
1933       0.018054      -0.018896      -0.036591      -0.012649   
1934       0.006866      -0.033137      -0.000402 

In [8]:
questions = embed_text(df_questions, 'deepvk/USER2-small', 'query')
questions

Encoding: 100%|██████████| 219/219 [00:30<00:00,  7.10it/s]
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_with_embeddings[embedding_columns] = result
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_with_embeddings[embedding_columns] = result
/var/folders/7v/l84v712d717cx757wmbslz440000gn/T/ipykernel_94783/1141303819.py:19: PerformanceWarning: DataFrame is highly

q_id                                              query  embedding_0  \
0        1                                        Номер счета    -0.132160   
1        2                              Где узнать бик и счёт     0.048114   
2        3  Мне не приходят коды для подтверждения данной ...    -0.109121   
3        4  Оформила рассрочку ,но уведомлений никаких не ...    -0.078583   
4        5  Здравствуйте, когда смогу пользоваться кредитн...    -0.074972   
...    ...                                                ...          ...   
6972  6973  Здравствуйте, оплатил вчера ЖКХ а кэшбек не на...    -0.040148   
6973  6974  Здравствуйте,  можно ли заказать реквизиты бан...    -0.037140   
6974  6975  Здравствуйте, подскажите пожалуйста где я могу...    -0.052637   
6975  6976                  Реквизиты для оплаты номера карты    -0.015533   
6976  6977  Можно ли отключить автопополнение брокерского ...     0.010994   

      embedding_1  embedding_2  embedding_3  embedding_4  embedding_5  \
0        0.048609     0.119710     0.026601     0.083500     0.152975   
1        0.043787     0.063055     0.043169     0.072952     0.248080   
2       -0.094989     0.078021     0.005559     0.036249     0.157940   
3        0.018154     0.085140    -0.009302     0.060945     0.120396   
4        0.035691     0.088600     0.129808     0.002700     0.098466   
...           ...          ...          ...          ...          ...   
6972    -0.010132     0.025507    -0.099721     0.011487     0.122394   
6973     0.070794     0.083746     0.010271     0.081852     0.148493   
6974     0.082618     0.155022    -0.032515     0.059243     0.136505   
6975     0.052458     0.116866     0.028701     0.011626     0.131102   
6976    -0.026624     0.070320    -0.000119     0.017202     0.060602   

      embedding_6  embedding_7  ...  embedding_374  embedding_375  \
0        0.125071    -0.089970  ...       0.001772       0.015677   
1        0.045151    -0.144925  ...      -0.007126       0.009204   
2        0.166196    -0.092763  ...      -0.001336       0.061428   
3        0.080605    -0.008345  ...       0.013107       0.007714   
4       -0.019188    -0.084034  ...       0.000825       0.005651   
...           ...          ...  ...            ...            ...   
6972     0.026245    -0.112670  ...       0.013485       0.043436   
6973     0.136672    -0.084124  ...      -0.003348       0.012676   
6974     0.070528    -0.081827  ...       0.010213      -0.003458   
6975     0.083497    -0.082694  ...       0.006458       0.009040   
6976    -0.003908    -0.082578  ...       0.018493       0.005623   

      embedding_376  embedding_377  embedding_378  embedding_379  \
0         -0.003718       0.015371       0.003344       0.003203   
1         -0.040645      -0.006170      -0.039395       0.011794   
2         -0.014644      -0.061347      -0.011018       0.012299   
3          0.002654      -0.012238       0.000596       0.024725   
4         -0.003132      -0.016272       0.004920       0.017115   
...             ...            ...            ...            ...   
6972      -0.029002      -0.027176      -0.031733      -0.007734   
6973      -0.015403      -0.034304       0.005483       0.014668   
6974       0.005165       0.014682      -0.019374       0.030802   
6975      -0.002602      -0.031060       0.023191       0.014807   
6976      -0.011058       0.025525      -0.002219       0.053172   

      embedding_380  embedding_381  embedding_382  embedding_383  
0         -0.009970      -0.034651      -0.012746       0.033362  
1          0.017990      -0.009951      -0.018796       0.031424  
2          0.022173      -0.006491      -0.021963      -0.017590  
3          0.025541      -0.003996      -0.023879      -0.056220  
4          0.007816      -0.037474      -0.007649       0.018453  
...             ...            ...            ...            ...  
6972       0.017985       0.008052      -0.003031      -0.038443  
6973      

In [9]:
def cosine_sim(df_sites, df_question):
    cols_sites = [col for col in df_sites.columns if col.startswith('embedding_')]
    cols_question = [col for col in df_question.columns if col.startswith('embedding_')]

    site_embeddings = df_sites[cols_sites].values
    question_embeddings = df_question[cols_question].values

    cosine_sim_matrix = cosine_similarity(question_embeddings, site_embeddings)

    results = []
    
    for i, (q_idx, question_row) in enumerate(tqdm(df_question.iterrows(), total=len(df_question), desc="Processing")):
        for j, (s_idx, site_row) in enumerate(df_sites.iterrows()):
            cosine_sim = cosine_sim_matrix[i, j]
            
            results.append({
                'q_id': question_row['q_id'],
                'web_id': site_row['web_id'],
                'query': question_row['query'],
                'site_text': site_row['text'],
                'cosine_similarity': cosine_sim
            })
    
    # Создаем финальный датафрейм
    cosine_df = pd.DataFrame(results)

    return cosine_df

In [ ]:
cosine_df = cosine_sim(sites, questions)

Processing:  33%|███▎      | 2268/6977 [01:16<02:31, 31.06it/s]

In [ ]:
cosine_df

q_id  web_id                                              query  \
0            1       1                                        Номер счета   
1            1       2                                        Номер счета   
2            1       3                                        Номер счета   
3            1       4                                        Номер счета   
4            1       5                                        Номер счета   
...        ...     ...                                                ...   
13521421  6977    1934  Можно ли отключить автопополнение брокерского ...   
13521422  6977    1935  Можно ли отключить автопополнение брокерского ...   
13521423  6977    1936  Можно ли отключить автопополнение брокерского ...   
13521424  6977    1937  Можно ли отключить автопополнение брокерского ...   
13521425  6977    1938  Можно ли отключить автопополнение брокерского ...   

                                                  site_text  cosine_similarity  
0         Рассчитайте выгоду\nРасчёт калькулятора предва...           0.623526  
1         Брокерские услуги\nОткрытие брокерского счёта ...           0.611694  
2         Хотите получить больше информации?\nПозвоните ...           0.637728  
3         Правила проведения Акции «Альфа Пятница. Бараб...           0.588181  
4         Образование\nМагистратуры\nМагистратура ВШЭ\nМ...           0.501138  
...                                                     ...                ...  
13521421  Возврат денег покупателю можно оформить через ...           0.646972  
13521422  Вывести деньги с брокерского счёта можно на ка...           0.738052  
13521423  Вывести деньги с брокерского счёта можно на сл...           0.727085  
13521424  Альфа-Смарт — семейная подписка, запущенная в ...           0.712945  
13521425                                                NaN           0.548250  

[13521426 rows x 5 columns]

In [ ]:
# Создаем датафрейм с топ-5 наиболее похожими сайтами для каждого вопроса
top5_df = cosine_df.groupby('q_id').apply(
    lambda x: x.nlargest(5, 'cosine_similarity')
).reset_index(drop=True)

In [ ]:
print(f"Размер датафрейма с топ-5: {top5_df.shape}")
print(top5_df.head(10))

# Функция для красивого вывода текстов
def format_text(text, max_length=200):
    if pd.isna(text):
        return "Текст отсутствует"
    text = str(text).strip()
    if len(text) > max_length:
        return text[:max_length] + "..."
    return text

# Выводим топ-5 сайтов для каждого вопроса
print("\n" + "="*100)
print("ТОП-5 САМЫХ ПОХОЖИХ САЙТОВ ДЛЯ КАЖДОГО ВОПРОСА:")
print("="*100)

for q_id in top5_df['q_id'].unique():
    question_data = top5_df[top5_df['q_id'] == q_id]
    
    # Берем первый вопрос из группы (они все одинаковые для данного q_id)
    query_text = question_data['query'].iloc[0]
    
    print(f"\n\nВОПРОС {q_id}: {query_text}")
    print("-" * 100)
    
    for i, (idx, row) in enumerate(question_data.iterrows(), 1):
        print(f"\n{i}. Сайт ID: {row['web_id']} | Косинусная схожесть: {row['cosine_similarity']:.4f}")
        print(f"   Текст сайта: {format_text(row['site_text'])}")
    
    print("\n" + "="*100)

Размер датафрейма с топ-5: (34885, 5)
   q_id  web_id                  query  \
0     1    1404            Номер счета   
1     1    1252            Номер счета   
2     1     501            Номер счета   
3     1    1567            Номер счета   
4     1     844            Номер счета   
5     2    1098  Где узнать бик и счёт   
6     2    1607  Где узнать бик и счёт   
7     2     372  Где узнать бик и счёт   
8     2    1659  Где узнать бик и счёт   
9     2    1080  Где узнать бик и счёт   

                                           site_text  cosine_similarity  
0  17.10.2017\nИнформация об изменениях: В связи ...           0.754181  
1  Счета и депозиты\nС 30 июня 2020 недоступен дл...           0.732902  
2  20.10.2017\nИнформация об изменениях: Был пере...           0.723508  
3  Ещё нужен номер карты\nНомер карты\nНомер карт...           0.717986  
4  Документы и тарифы\nЗдесь вы найдете документы...           0.714746  
5  Альфа-Банк\nПолезное о продуктах\nIBAN (Intern...   

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
top5_df

q_id  web_id                                              query  \
0         1    1404                                        Номер счета   
1         1    1252                                        Номер счета   
2         1     501                                        Номер счета   
3         1    1567                                        Номер счета   
4         1     844                                        Номер счета   
...     ...     ...                                                ...   
34880  6977     438  Можно ли отключить автопополнение брокерского ...   
34881  6977    1107  Можно ли отключить автопополнение брокерского ...   
34882  6977    1272  Можно ли отключить автопополнение брокерского ...   
34883  6977    1579  Можно ли отключить автопополнение брокерского ...   
34884  6977    1270  Можно ли отключить автопополнение брокерского ...   

                                               site_text  cosine_similarity  
0      17.10.2017\nИнформация об изменениях: В связи ...           0.754181  
1      Счета и депозиты\nС 30 июня 2020 недоступен дл...           0.732902  
2      20.10.2017\nИнформация об изменениях: Был пере...           0.723508  
3      Ещё нужен номер карты\nНомер карты\nНомер карт...           0.717986  
4      Документы и тарифы\nЗдесь вы найдете документы...           0.714746  
...                                                  ...                ...  
34880  Как открыть брокерский счёт? Сколько времени н...           0.780381  
34881  Альфа-Банк\nПолезное о продуктах\nБрокерские с...           0.758086  
34882  Сколько стоит обслуживание брокерского счёта в...           0.756307  
34883  В соответствии с требованиями Указания Банка Р...           0.756242  
34884  Как получить документы об открытии брокерского...           0.754996  

[34885 rows x 5 columns]

In [ ]:
# Создаем датафрейм с web_list для каждого q_id
web_list_df = top5_df.groupby('q_id')['web_id'].apply(list).reset_index()
web_list_df.columns = ['q_id', 'web_list']

print("Датафрейм с web_list:")
print(web_list_df.head(10))
print(f"\nРазмер датафрейма: {web_list_df.shape}")

Датафрейм с web_list:
   q_id                       web_list
0     1   [1404, 1252, 501, 1567, 844]
1     2  [1098, 1607, 372, 1659, 1080]
2     3    [856, 116, 1724, 114, 1604]
3     4  [1043, 1680, 1590, 1924, 478]
4     5  [927, 1029, 1909, 1193, 1033]
5     6    [1929, 1592, 891, 688, 697]
6     7    [1252, 1470, 810, 808, 372]
7     8   [1673, 904, 1726, 898, 1677]
8     9  [1193, 927, 1340, 1909, 1894]
9    10    [454, 1884, 114, 455, 1924]

Размер датафрейма: (6977, 2)


In [ ]:
# Преобразуем списки в строки, которые выглядят как массивы
web_list_df = top5_df.groupby('q_id')['web_id'].apply(
    lambda x: "[" + ", ".join(map(str, x.tolist())) + "]"
).reset_index()
web_list_df.columns = ['q_id', 'web_list']

print("Датафрейм с web_list в виде строк:")
print(web_list_df.head(10))
print(f"\nРазмер датафрейма: {web_list_df.shape}")

# Проверим тип данных
print(f"\nТип данных web_list: {web_list_df['web_list'].dtype}")
print(f"Тип первого элемента: {type(web_list_df['web_list'].iloc[0])}")
print(f"Пример содержимого: {web_list_df['web_list'].iloc[0]}")

Датафрейм с web_list в виде строк:
   q_id                       web_list
0     1   [1404, 1252, 501, 1567, 844]
1     2  [1098, 1607, 372, 1659, 1080]
2     3    [856, 116, 1724, 114, 1604]
3     4  [1043, 1680, 1590, 1924, 478]
4     5  [927, 1029, 1909, 1193, 1033]
5     6    [1929, 1592, 891, 688, 697]
6     7    [1252, 1470, 810, 808, 372]
7     8   [1673, 904, 1726, 898, 1677]
8     9  [1193, 927, 1340, 1909, 1894]
9    10    [454, 1884, 114, 455, 1924]

Размер датафрейма: (6977, 2)

Тип данных web_list: object
Тип первого элемента: <class 'str'>
Пример содержимого: [1404, 1252, 501, 1567, 844]


In [ ]:
web_list_df.to_csv('submit_1.csv', index=False)